In [7]:
#imported the library or packages we need over the all sections

from apikeys import my_api_key
import requests
import json
import numpy as np
import pandas as pd
import nltk
import re
from nltk.tokenize import TweetTokenizer, sent_tokenize
from nltk.stem.snowball import SnowballStemmer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.cluster import KMeans
import seaborn as sns
import matplotlib.pyplot as plt
from sklearn.metrics.pairwise import cosine_similarity
import math as m
from scipy.cluster.hierarchy import linkage 
from scipy.cluster.hierarchy import dendrogram
%matplotlib inline
import matplotlib.pyplot as plt
import pandas as pd

In [5]:
# Pull out the genre list
def get_genre_list(my_api_key):
    '''Define a function that takes my_api_key as argument, 
       acess the API of IMDB,
       get the genre information, 
       and output the genre list '''
    genre_1 = requests.get("https://api.themoviedb.org/3/genre/movie/list?api_key="+my_api_key+"&language=en-US")
    genre_2 = genre_1.json()
    genre_list = genre_2['genres']
    return genre_list
genre_list=get_genre_list(my_api_key)

In [260]:
len(genre_list)

19

In [8]:
genre_df = pd.DataFrame(genre_list)

In [128]:
genre_df

id             name
0      28           Action
1      12        Adventure
2      16        Animation
3      35           Comedy
4      80            Crime
5      99      Documentary
6      18            Drama
7   10751           Family
8      14          Fantasy
9      36          History
10     27           Horror
11  10402            Music
12   9648          Mystery
13  10749          Romance
14    878  Science Fiction
15  10770         TV Movie
16     53         Thriller
17  10752              War
18     37          Western

In [11]:
genre_df.to_csv('data/genre.csv', index=False)

In [42]:
# Pull out the movie list from released year 2020
# &include_video=false&language=en-US&primary_release_date.gte=2020-01-01&primary_release_date.lte=2020-05-31
def get_movie_list(my_api_key):
    '''Define a function that takes my_api_key as argument, 
       acess the API of IMDB,
       get the all the movie information, 
       and output the movie list including the rating, title, genre, and overview of all the movies in 2020 '''
    movie_1 = requests.get("https://api.themoviedb.org/3/discover/movie?api_key="+my_api_key+"&include_adult=false&primary_release_year=2020&language=en-US")
    movie_2 = movie_1.json()
    page_number = movie_2['total_pages']
    movie_number = movie_2['total_results']
    movie_list = []
    for n in range(1,page_number+1):
        movie_3 = requests.get("https://api.themoviedb.org/3/discover/movie?api_key="+my_api_key+"&include_adult=false&primary_release_year=2020&page=%s"%n)
        movie_4 = movie_3.json()
        movie_result = movie_4['results']
        for item in movie_result:
            movie_list.append({'id':item['id'], 
                               "vote_average": item["vote_average"], 
                               "title": item["title"], 
                               "genre_ids": item["genre_ids"], 
                               "overview": item["overview"], 
                               'popularity':item['popularity'], 
                               'original_language':item['original_language'], 
                               'release_date':item['release_date']})
    return movie_list     
movie_list=get_movie_list(my_api_key)

KeyError: 'production_companies'

In [41]:
pd.DataFrame(movie_list)

id  vote_average                      title  \
0     338762           7.1                  Bloodshot   
1     385103           8.2                     Scoob!   
2     582596           6.2            The Wrong Missy   
3     454626           7.6         Sonic the Hedgehog   
4     508439           7.9                     Onward   
...      ...           ...                        ...   
6335  705637           0.0                Sugarbabies   
6336  705625           0.0  The Final Years of Majuro   
6337  705617           0.0             Hips Don't Lie   
6338  704828           0.0                   Lockdown   
6339  701773           0.0             Hidden Windows   

                      genre_ids  \
0                 [28, 18, 878]   
1     [12, 16, 35, 9648, 10751]   
2                   [35, 10749]   
3          [28, 35, 878, 10751]   
4       [12, 16, 35, 14, 10751]   
...                         ...   
6335                         []   
6336                       [99]   
6337                       [35]   
6338                       [53]   
6339                       [99]   

                                               overview  popularity  \
0     After he and his wife are murdered, marine Ray...     206.878   
1     In Scooby-Doo’s greatest adventure yet, see th...     253.085   
2     A guy meets the woman of his dreams and invite...     130.525   
3     Based on the global blockbuster videogame fran...     130.190   
4     In a suburban fantasy world, two teenage elf b...     108.591   
...                                                 ...         ...   
6335  Desperate Glenn will do anything to hold on to...       0.717   
6336  Land is supposed to be the embodiment of perma...       1.400   
6337  A comedy about the sexy and lovely growth of a...       1.083   
6338  A man who doesn't remember anything wakes up i...       0.000   
6339                                                          0.000   

     original_language release_date  
0                   en   2020-03-05  
1                   en   2020-05-15  
2                   en   2020-05-13  
3                   en   2020-02-12  
4                   en   2020-02-29  
...                ...          ...  
6335                en   2020-02-25  
6336                en   2020-05-05  
6337                ko   2020-12-31  
6338                id   2020-05-15  
6339                en   2020-05-08  

[6340 rows x 8 columns]

In [34]:
movie_1 = requests.get("https://api.themoviedb.org/3/discover/movie?api_key="+my_api_key+"&include_adult=false&primary_release_date.gte=2020-01-01&primary_release_date.lte=2020-05-31&language=en-US")

In [36]:
movie_2 = movie_1.json()

In [37]:
movie_2

{'page': 1,
 'total_results': 5596,
 'total_pages': 280,
 'results': [{'popularity': 206.878,
   'vote_count': 2300,
   'video': False,
   'poster_path': '/8WUVHemHFH2ZIP6NWkwlHWsyrEL.jpg',
   'id': 338762,
   'adult': False,
   'backdrop_path': '/ocUrMYbdjknu2TwzMHKT9PBBQRw.jpg',
   'original_language': 'en',
   'original_title': 'Bloodshot',
   'genre_ids': [28, 18, 878],
   'title': 'Bloodshot',
   'vote_average': 7.1,
   'overview': "After he and his wife are murdered, marine Ray Garrison is resurrected by a team of scientists. Enhanced with nanotechnology, he becomes a superhuman, biotech killing machine—'Bloodshot'. As Ray first trains with fellow super-soldiers, he cannot recall anything from his former life. But when his memories flood back and he remembers the man that killed both him and his wife, he breaks out of the facility to get revenge, only to discover that there's more to the conspiracy than he thought.",
   'release_date': '2020-03-05'},
  {'popularity': 253.085,
   

In [35]:
movie_1

<Response [200]>

In [18]:
my_api_key

'81c0a8cc3f4d402b937eb21fc671a5c4'

In [137]:
movie_1 = requests.get("https://api.themoviedb.org/3/discover/movie?api_key="+my_api_key+"&include_adult=false&primary_release_date.gte=2020-01-01&primary_release_date.lte=2020-05-31&language=en-US")

In [138]:
movie_2 = movie_1.json()

In [139]:
page_number = movie_2['total_pages']
movie_number = movie_2['total_results']
movie_id_list = []

In [141]:
for n in range(1,page_number+1):
    movie_3 = requests.get("https://api.themoviedb.org/3/discover/movie?api_key="+my_api_key+"&include_adult=false&language=en-US&primary_release_year=2020&page=%s"%n)
    movie_4 = movie_3.json()
    movie_result = movie_4['results']
    for item in movie_result:
        movie_id_list.append({'id':item['id']})

In [142]:
len(movie_id_list)

5640

In [143]:
movie_id_list[1]

{'id': 338762}

In [144]:
%%time
movie_info_list = []
for n in movie_id_list:
    movie_5 = requests.get("https://api.themoviedb.org/3/movie/"+str(n['id'])+"?api_key="+my_api_key)
    movie_6 = movie_5.json()
    movie_info_list.append(movie_6)

CPU times: user 2min 3s, sys: 8.4 s, total: 2min 12s
Wall time: 22min 41s


In [152]:
movie_info_list

[{'adult': False,
  'backdrop_path': '/b5Fej0UT6gPFd2GcGEWw4SAwGUM.jpg',
  'belongs_to_collection': None,
  'budget': 0,
  'genres': [{'id': 10751, 'name': 'Family'},
   {'id': 16, 'name': 'Animation'},
   {'id': 35, 'name': 'Comedy'},
   {'id': 9648, 'name': 'Mystery'},
   {'id': 12, 'name': 'Adventure'}],
  'homepage': 'https://www.scoob.movie/',
  'id': 385103,
  'imdb_id': 'tt3152592',
  'original_language': 'en',
  'original_title': 'Scoob!',
  'overview': 'In Scooby-Doo’s greatest adventure yet, see the never-before told story of how lifelong friends Scooby and Shaggy first met and how they joined forces with young detectives Fred, Velma, and Daphne to form the famous Mystery Inc. Now, with hundreds of cases solved, Scooby and the gang face their biggest, toughest mystery ever: an evil plot to unleash the ghost dog Cerberus upon the world. As they race to stop this global “dogpocalypse,” the gang discovers that Scooby has a secret legacy and an epic destiny greater than anyone ev

In [95]:
movie_info_list[1]['production_companies'] == [{'id': 25120,
  'logo_path': '/lqUpBvDLQYG3QaKNpe2lxfpgh36.png',
  'name': 'Warner Animation Group',
  'origin_country': 'US'},
 {'id': 174,
  'logo_path': '/IuAlhI9eVC9Z8UQWOIDdWRKSEJ.png',
  'name': 'Warner Bros. Pictures',
  'origin_country': 'US'}]

True

In [114]:
movie_info_list[922]

{'adult': False,
 'backdrop_path': '/dSPVnJhHjQXHxQmajpTJgQE9aO8.jpg',
 'belongs_to_collection': None,
 'budget': 0,
 'genres': [{'id': 35, 'name': 'Comedy'}],
 'homepage': '',
 'id': 658156,
 'imdb_id': 'tt10966156',
 'original_language': 'fr',
 'original_title': 'Lucky',
 'overview': '',
 'popularity': 4.627,
 'poster_path': '/9sSgcTIHrm4kSDh5FnQGIsGfbeb.jpg',
 'production_companies': [{'id': 12407,
   'logo_path': None,
   'name': 'Panache Productions',
   'origin_country': 'BE'},
  {'id': 62546,
   'logo_path': None,
   'name': '2.4.7. Films',
   'origin_country': 'FR'},
  {'id': 127965,
   'logo_path': None,
   'name': 'Compagnie Cinématographique, La',
   'origin_country': ''},
  {'id': 55248,
   'logo_path': None,
   'name': 'Tchin Tchin Productions',
   'origin_country': ''}],
 'production_countries': [{'iso_3166_1': 'FR', 'name': 'France'}],
 'release_date': '2020-02-26',
 'revenue': 0,
 'runtime': 0,
 'spoken_languages': [{'iso_639_1': 'fr', 'name': 'Français'}],
 'status': '

In [94]:
for n in range(len(movie_info_list)):
    
#     if movie_info_list[n]["production_companies"] == [{'id': 12407, 'logo_path': None, 'name': 'Panache Productions', 'origin_country': 'BE'}, {'id': 62546, 'logo_path': None, 'name': '2.4.7. Films', 'origin_country': 'FR'}, {'id': 127965, 'logo_path': None, 'name': 'Compagnie Cinématographique, La', 'origin_country': ''}, {'id': 55248, 'logo_path': None, 'name': 'Tchin Tchin Productions', 'origin_country': ''}]:
#         print(n)

922


KeyError: 'production_companies'

In [145]:
%%time
production_companies_list = []
for i in movie_info_list:
    if i != {'status_code': 34,
 'status_message': 'The resource you requested could not be found.'}:
        for n in i['production_companies']:
            production_companies_list.append(n)


CPU times: user 7.64 ms, sys: 81.7 ms, total: 89.3 ms
Wall time: 239 ms


In [146]:
production_companies_df = pd.DataFrame(production_companies_list).drop_duplicates()

In [147]:
production_companies_df

id                         logo_path                           name  \
0      25120  /lqUpBvDLQYG3QaKNpe2lxfpgh36.png         Warner Animation Group   
1        174   /IuAlhI9eVC9Z8UQWOIDdWRKSEJ.png          Warner Bros. Pictures   
2         34   /GagSvqWlyPdkFHMfQ3pNq6ix9P.png                  Sony Pictures   
3      10246  /rREvQNWAxkDfY9CDn2c5YxEMPdP.png           Cross Creek Pictures   
4       6573                              None          Mimran Schur Pictures   
...      ...                               ...                            ...   
4780  100251                              None  Aggressively Okay Productions   
4781  129139                              None                  Goaty Studios   
4782  112076                              None      Aesthetic Rebellion Films   
4783  121241                              None                 MD Productions   
4786   83226                              None                     VAIT FILMS   

     origin_country  
0                US  
1                US  
2                US  
3                US  
4                US  
...             ...  
4780                 
4781                 
4782                 
4783                 
4786                 

[3509 rows x 4 columns]

In [148]:
production_companies_df.to_csv('data/production_companies_010120_050120.csv', index=False)

In [149]:
%%time
language_list = []
for i in movie_info_list:
    if i != {'status_code': 34,
 'status_message': 'The resource you requested could not be found.'}:
        for n in i['spoken_languages']:
            language_list.append(n)


CPU times: user 7.37 ms, sys: 44.2 ms, total: 51.6 ms
Wall time: 105 ms


In [150]:
language_df = pd.DataFrame(language_list).drop_duplicates()

In [151]:
language_df

iso_639_1      name
0           en   English
4           bn     বাংলা
6           hi    हिन्दी
13          es   Español
15          it  Italiano
...        ...       ...
4016        gd          
4112        uz     ozbek
4424        gn          
4439        xh          
4491        ha     Hausa

[98 rows x 2 columns]

In [153]:
language_df.to_csv('data/language_010120_050120.csv', index=False)

In [154]:
movie_list = []
for item in movie_info_list:
    if item != {'status_code': 34,
 'status_message': 'The resource you requested could not be found.'}:
        movie_list.append({'id': item['id'], 
                           "vote_average": item["vote_average"], 
                           'vote_count': item['vote_count'],
                           "title": item["title"], 
                           "genre_id": [n['id'] for n in item["genres"]], 
                           "overview": item["overview"], 
                           'popularity': item['popularity'], 
                           'original_language': item['original_language'], 
                           'release_date': item['release_date'], 
                           "production_companies_id": [n['id'] for n in item["production_companies"]], 
                           "homepage": item["homepage"], 
                           "imdb_id": item["imdb_id"], 
                           "revenue": item["revenue"], 
                           "tagline": item["tagline"]})

In [155]:
len(movie_list)

5632

In [156]:
movie_list

[{'id': 385103,
  'vote_average': 8.2,
  'vote_count': 453,
  'title': 'Scoob!',
  'genre_id': [10751, 16, 35, 9648, 12],
  'overview': 'In Scooby-Doo’s greatest adventure yet, see the never-before told story of how lifelong friends Scooby and Shaggy first met and how they joined forces with young detectives Fred, Velma, and Daphne to form the famous Mystery Inc. Now, with hundreds of cases solved, Scooby and the gang face their biggest, toughest mystery ever: an evil plot to unleash the ghost dog Cerberus upon the world. As they race to stop this global “dogpocalypse,” the gang discovers that Scooby has a secret legacy and an epic destiny greater than anyone ever imagined.',
  'popularity': 253.085,
  'original_language': 'en',
  'release_date': '2020-05-15',
  'production_companies_id': [25120, 174],
  'homepage': 'https://www.scoob.movie/',
  'imdb_id': 'tt3152592',
  'revenue': 0,
  'tagline': 'Mystery Loves Company.'},
 {'id': 338762,
  'vote_average': 7.1,
  'vote_count': 2314,
 

In [157]:
movie_df = pd.DataFrame(movie_list)

In [159]:
movie_en_df = movie_df[movie_df['original_language']=='en']

In [160]:
movie_en_df.to_csv('data/movie_010120_050120.csv', index=False)

In [127]:
%%time
similar_movie_list = []
for n in movie_id_list:
    s_movie_req = requests.get("https://api.themoviedb.org/3/movie/"+str(n['id'])+"similar?api_key="+my_api_key)
    s_movie_req_j = s_movie_req.json()
    similar_movie_list.append(s_movie_req_j)

CPU times: user 1min 59s, sys: 8.45 s, total: 2min 7s
Wall time: 44min 7s


In [161]:
similar_movie_list

[{'adult': False,
  'backdrop_path': '/ocUrMYbdjknu2TwzMHKT9PBBQRw.jpg',
  'belongs_to_collection': None,
  'budget': 42000000,
  'genres': [{'id': 28, 'name': 'Action'},
   {'id': 878, 'name': 'Science Fiction'},
   {'id': 18, 'name': 'Drama'}],
  'homepage': 'https://www.bloodshot.movie/',
  'id': 338762,
  'imdb_id': 'tt1634106',
  'original_language': 'en',
  'original_title': 'Bloodshot',
  'overview': "After he and his wife are murdered, marine Ray Garrison is resurrected by a team of scientists. Enhanced with nanotechnology, he becomes a superhuman, biotech killing machine—'Bloodshot'. As Ray first trains with fellow super-soldiers, he cannot recall anything from his former life. But when his memories flood back and he remembers the man that killed both him and his wife, he breaks out of the facility to get revenge, only to discover that there's more to the conspiracy than he thought.",
  'popularity': 206.878,
  'poster_path': '/8WUVHemHFH2ZIP6NWkwlHWsyrEL.jpg',
  'production_c

In [162]:
s_movie_info_list = []
for item in similar_movie_list:
    if item != {'status_code': 34,
 'status_message': 'The resource you requested could not be found.'}:
        s_movie_info_list.append({'id': item['id'], 
                           "vote_average": item["vote_average"], 
                           'vote_count': item['vote_count'],
                           "title": item["title"], 
                           "genre_id": [n['id'] for n in item["genres"]], 
                           "overview": item["overview"], 
                           'popularity': item['popularity'], 
                           'original_language': item['original_language'], 
                           'release_date': item['release_date'], 
                           "production_companies_id": [n['id'] for n in item["production_companies"]], 
                           "homepage": item["homepage"], 
                           "imdb_id": item["imdb_id"], 
                           "revenue": item["revenue"], 
                           "tagline": item["tagline"]})

In [176]:
s_movie_info_df = pd.DataFrame(s_movie_info_list)

In [178]:
s_movie_info_df.drop_duplicates(subset ="id", 
                                keep = False, inplace = True)

In [180]:
s_movie_info_df

id  vote_average  vote_count  \
0     338762           7.1        2314   
1     385103           8.2         458   
2     582596           6.2         200   
3     454626           7.5        4003   
4     508439           7.9        1826   
...      ...           ...         ...   
5587  671997           0.0           0   
5588  671907           0.0           0   
5589  671901           0.0           0   
5590  671897           0.0           0   
5591  671895           0.0           0   

                                        title                   genre_id  \
0                                   Bloodshot              [28, 878, 18]   
1                                      Scoob!  [10751, 16, 35, 9648, 12]   
2                             The Wrong Missy                [35, 10749]   
3                          Sonic the Hedgehog       [28, 878, 35, 10751]   
4                                      Onward    [16, 10751, 12, 35, 14]   
...                                       ...                        ...   
5587  Crónica macabra de una noche cualquiera               [27, 35, 14]   
5588                   Moments Before Sundown                   [99, 18]   
5589                             4EVER [Love]               [10749, 878]   
5590                                  Equinox                         []   
5591                             Tatsuniya II                         []   

                                               overview  popularity  \
0     After he and his wife are murdered, marine Ray...     206.878   
1     In Scooby-Doo’s greatest adventure yet, see th...     253.085   
2     A guy meets the woman of his dreams and invite...     130.525   
3     Based on the global blockbuster videogame fran...     130.190   
4     In a suburban fantasy world, two teenage elf b...     108.591   
...                                                 ...         ...   
5587                                                          0.600   
5588  Over the course of 4 months, we follow a group...       0.600   
5589  A short film about the beginning of an endless...       0.600   
5590  Made by exposing a standard roll of print stoc...       0.600   
5591  A group of students at the Shehu Sanda Kyarimi...       0.600   

     original_language release_date  \
0                   en   2020-03-05   
1                   en   2020-05-15   
2                   en   2020-05-13   
3                   en   2020-02-12   
4                   en   2020-02-29   
...                ...          ...   
5587                es   2020-10-10   
5588                en   2020-02-11   
5589                es   2020-02-14   
5590                en   2020-02-23   
5591                ha   2020-02-22   

                                production_companies_id  \
0     [34, 10246, 6573, 333, 103673, 124335, 5, 1225...   
1                                          [25120, 174]   
2                                 [2608, 133986, 72725]   
3         [333, 10644, 77884, 4, 113750, 100711, 24955]   
4                                                [2, 3]   
...                                                 ...   
5587                                                 []   
5588                                                 []   
5589                                                 []   
5590                                                 []   
5591                                                 []   

                                               homepage    imdb_id    revenue  \
0                          https://www.bloodshot.movie/  tt1634106   24573617   
1                              https://www.scoob.movie/  tt3152592          0   
2                https://www.netflix.com/title/81033865  tt9619798          0   
3     https://www.paramountmovies.com/movies/sonic-t...  tt3794354  306766470   
4                                                        tt7146812  103181419   
...                                                 ...        ...        .

In [211]:
t1 = requests.get("https://api.themoviedb.org/3/movie/701515/similar?api_key="+my_api_key+"&include_adult=false&language=en-US&page=%s"%3)
t2 = t1.json()

# get similar movies

In [212]:
t2

{'status_code': 34,
 'status_message': 'The resource you requested could not be found.'}

In [213]:
%%time
similar_movie_id_dict_list = []
for n in movie_id_list:
    s_movie_req = requests.get("https://api.themoviedb.org/3/movie/"+str(n['id'])+"/similar?api_key="+my_api_key+"&include_adult=false&language=en-US")
    s_movie_req_j = s_movie_req.json()
    if s_movie_req_j != {'status_code': 34, 'status_message': 'The resource you requested could not be found.'}:
        similar_page_number = s_movie_req_j['total_pages']
        similar_movie_number = s_movie_req_j['total_results']
        similar_movie_id_list = []
        print(n)
        if similar_page_number >=5:
            for i in range(1,6):
                s_movie_1 = requests.get("https://api.themoviedb.org/3/movie/"+str(n['id'])+"/similar?api_key="+my_api_key+"&include_adult=false&language=en-US&page=%s"%i)
                s_movie_2 = s_movie_1.json()
                s_movie_result = s_movie_2['results']
                for item in s_movie_result:
                    similar_movie_id_list.append(item['id'])
        else:
            for i in range(1,similar_page_number+1):
                s_movie_1 = requests.get("https://api.themoviedb.org/3/movie/"+str(n['id'])+"/similar?api_key="+my_api_key+"&include_adult=false&language=en-US&page=%s"%i)
                s_movie_2 = s_movie_1.json()
                s_movie_result = s_movie_2['results']
                for item in s_movie_result:
                    similar_movie_id_list.append(item['id'])
        similar_movie_id_dict_list.append({'id':n['id'], 'similar_movie_id':similar_movie_id_list})
    

{'id': 385103}
{'id': 338762}
{'id': 582596}
{'id': 454626}
{'id': 545609}
{'id': 495764}
{'id': 618344}
{'id': 508439}
{'id': 570670}
{'id': 481848}
{'id': 38700}
{'id': 429422}
{'id': 443791}
{'id': 691812}
{'id': 448119}
{'id': 539537}
{'id': 514847}
{'id': 446893}
{'id': 642657}
{'id': 701369}
{'id': 624808}
{'id': 522627}
{'id': 701684}
{'id': 592834}
{'id': 529485}
{'id': 669770}
{'id': 556678}
{'id': 597219}
{'id': 698320}
{'id': 664767}
{'id': 542224}
{'id': 567608}
{'id': 645181}
{'id': 644092}
{'id': 689723}
{'id': 581600}
{'id': 605804}
{'id': 465086}
{'id': 541305}
{'id': 521007}
{'id': 466622}
{'id': 449756}
{'id': 501395}
{'id': 683311}
{'id': 585244}
{'id': 602147}
{'id': 681638}
{'id': 555974}
{'id': 548473}
{'id': 696575}
{'id': 323144}
{'id': 666750}
{'id': 627725}
{'id': 492611}
{'id': 502425}
{'id': 639908}
{'id': 682134}
{'id': 614292}
{'id': 523977}
{'id': 665251}
{'id': 560391}
{'id': 567598}
{'id': 342470}
{'id': 653744}
{'id': 482273}
{'id': 701675}
{'id': 6862

{'id': 676619}
{'id': 623266}
{'id': 579792}
{'id': 685495}
{'id': 665772}
{'id': 699465}
{'id': 339095}
{'id': 667177}
{'id': 643882}
{'id': 661728}
{'id': 553604}
{'id': 620883}
{'id': 670266}
{'id': 623926}
{'id': 606787}
{'id': 664413}
{'id': 675467}
{'id': 661329}
{'id': 642700}
{'id': 701197}
{'id': 581522}
{'id': 527400}
{'id': 653572}
{'id': 662212}
{'id': 690545}
{'id': 552532}
{'id': 664601}
{'id': 591629}
{'id': 157438}
{'id': 682598}
{'id': 639137}
{'id': 678856}
{'id': 525428}
{'id': 700104}
{'id': 661804}
{'id': 458673}
{'id': 584634}
{'id': 606234}
{'id': 597231}
{'id': 522444}
{'id': 616651}
{'id': 539565}
{'id': 604822}
{'id': 613785}
{'id': 668291}
{'id': 680980}
{'id': 629176}
{'id': 638706}
{'id': 638741}
{'id': 593655}
{'id': 691066}
{'id': 677210}
{'id': 693158}
{'id': 617502}
{'id': 535297}
{'id': 643205}
{'id': 674779}
{'id': 599281}
{'id': 571625}
{'id': 674942}
{'id': 547017}
{'id': 547012}
{'id': 623962}
{'id': 647785}
{'id': 690101}
{'id': 639514}
{'id': 694

{'id': 663870}
{'id': 651838}
{'id': 673306}
{'id': 693864}
{'id': 574089}
{'id': 579558}
{'id': 698362}
{'id': 672992}
{'id': 600354}
{'id': 671502}
{'id': 693699}
{'id': 702829}
{'id': 682514}
{'id': 648696}
{'id': 686158}
{'id': 700952}
{'id': 681711}
{'id': 655431}
{'id': 701925}
{'id': 590404}
{'id': 673640}
{'id': 696507}
{'id': 679694}
{'id': 702942}
{'id': 673496}
{'id': 659676}
{'id': 691911}
{'id': 615761}
{'id': 680734}
{'id': 614179}
{'id': 703237}
{'id': 694938}
{'id': 425001}
{'id': 677151}
{'id': 677646}
{'id': 615643}
{'id': 674358}
{'id': 662059}
{'id': 649368}
{'id': 623409}
{'id': 661095}
{'id': 666831}
{'id': 696357}
{'id': 700502}
{'id': 679150}
{'id': 702837}
{'id': 483157}
{'id': 674664}
{'id': 653664}
{'id': 688419}
{'id': 699340}
{'id': 627616}
{'id': 585245}
{'id': 690848}
{'id': 599333}
{'id': 603673}
{'id': 680956}
{'id': 611292}
{'id': 652004}
{'id': 548170}
{'id': 661701}
{'id': 558582}
{'id': 600136}
{'id': 694527}
{'id': 663635}
{'id': 616214}
{'id': 539

{'id': 698424}
{'id': 680631}
{'id': 676316}
{'id': 666509}
{'id': 642401}
{'id': 612495}
{'id': 701263}
{'id': 662072}
{'id': 673368}
{'id': 680252}
{'id': 618206}
{'id': 461479}
{'id': 691802}
{'id': 642678}
{'id': 701825}
{'id': 684542}
{'id': 672042}
{'id': 656185}
{'id': 665385}
{'id': 629522}
{'id': 705573}
{'id': 705559}
{'id': 705494}
{'id': 705493}
{'id': 705466}
{'id': 705457}
{'id': 705455}
{'id': 705454}
{'id': 705453}
{'id': 705444}
{'id': 705443}
{'id': 705438}
{'id': 705436}
{'id': 705433}
{'id': 705431}
{'id': 705426}
{'id': 705424}
{'id': 705419}
{'id': 705416}
{'id': 705414}
{'id': 705413}
{'id': 705410}
{'id': 705400}
{'id': 705399}
{'id': 705397}
{'id': 705396}
{'id': 705388}
{'id': 705385}
{'id': 705380}
{'id': 705379}
{'id': 705375}
{'id': 705372}
{'id': 705368}
{'id': 705354}
{'id': 705353}
{'id': 705343}
{'id': 705342}
{'id': 705341}
{'id': 705337}
{'id': 705336}
{'id': 705329}
{'id': 705326}
{'id': 705264}
{'id': 705227}
{'id': 705219}
{'id': 705214}
{'id': 705

{'id': 694973}
{'id': 664478}
{'id': 504409}
{'id': 694943}
{'id': 700270}
{'id': 703134}
{'id': 680593}
{'id': 676623}
{'id': 698265}
{'id': 617708}
{'id': 703504}
{'id': 679677}
{'id': 576716}
{'id': 700027}
{'id': 530351}
{'id': 513389}
{'id': 619083}
{'id': 681580}
{'id': 690991}
{'id': 682618}
{'id': 581577}
{'id': 690935}
{'id': 672300}
{'id': 647456}
{'id': 653659}
{'id': 670425}
{'id': 684246}
{'id': 673220}
{'id': 654107}
{'id': 647679}
{'id': 562600}
{'id': 510631}
{'id': 676148}
{'id': 579824}
{'id': 548647}
{'id': 518721}
{'id': 690544}
{'id': 671902}
{'id': 649719}
{'id': 539048}
{'id': 491630}
{'id': 686830}
{'id': 674577}
{'id': 518975}
{'id': 689154}
{'id': 609229}
{'id': 425651}
{'id': 705933}
{'id': 705924}
{'id': 705921}
{'id': 705893}
{'id': 705884}
{'id': 705729}
{'id': 705728}
{'id': 705692}
{'id': 705680}
{'id': 705676}
{'id': 705641}
{'id': 705625}
{'id': 705515}
{'id': 705482}
{'id': 704953}
{'id': 704750}
{'id': 704748}
{'id': 704745}
{'id': 704743}
{'id': 704

...

{'id': 571468}
{'id': 697587}
{'id': 697293}
{'id': 679785}
{'id': 704842}
{'id': 612513}
{'id': 674503}
{'id': 667910}
{'id': 677100}
{'id': 426242}
{'id': 681781}
{'id': 642751}
{'id': 616331}
{'id': 699043}
{'id': 573956}
{'id': 697770}
{'id': 694197}
{'id': 617106}
{'id': 617004}
{'id': 616982}
{'id': 616980}
{'id': 615433}
{'id': 596247}
{'id': 667015}
{'id': 698992}
{'id': 702842}
{'id': 672610}
{'id': 611751}
{'id': 670338}
{'id': 696909}
{'id': 696527}
{'id': 696207}
{'id': 693872}
{'id': 675866}
{'id': 598826}
{'id': 575774}
{'id': 683299}
{'id': 680170}
{'id': 684301}
{'id': 697620}
{'id': 692370}
{'id': 685050}
{'id': 682436}
{'id': 697019}
{'id': 696982}
{'id': 687378}
{'id': 698052}
{'id': 696873}
{'id': 611395}
{'id': 411326}
{'id': 697221}
{'id': 697088}
{'id': 696678}
{'id': 693495}
{'id': 669965}
{'id': 588099}
{'id': 692549}
{'id': 681734}
{'id': 680495}
{'id': 556270}
{'id': 703753}
{'id': 702156}
{'id': 701398}
{'id': 701224}
{'id': 701222}
{'id': 701221}
{'id': 701

{'id': 690150}
{'id': 701194}
{'id': 690109}
{'id': 682427}
{'id': 697390}
{'id': 672180}
{'id': 681749}
{'id': 692517}
{'id': 677068}
{'id': 669623}
{'id': 551405}
{'id': 705441}
{'id': 703490}
{'id': 702557}
{'id': 696203}
{'id': 696072}
{'id': 692478}
{'id': 684797}
{'id': 669171}
{'id': 666088}
{'id': 658287}
{'id': 612995}
{'id': 611652}
{'id': 610908}
{'id': 610351}
{'id': 608232}
{'id': 607365}
{'id': 607102}
{'id': 598354}
{'id': 597942}
{'id': 597688}
{'id': 595993}
{'id': 595464}
{'id': 595327}
{'id': 594640}
{'id': 592789}
{'id': 592782}
{'id': 590397}
{'id': 589972}
{'id': 587610}
{'id': 586947}
{'id': 586047}
{'id': 584249}
{'id': 582925}
{'id': 582877}
{'id': 579828}
{'id': 576922}
{'id': 575293}
{'id': 574080}
{'id': 572430}
{'id': 566953}
{'id': 554433}
{'id': 530395}
{'id': 493862}
{'id': 440361}
{'id': 417841}
{'id': 396194}
{'id': 365657}
{'id': 696831}
{'id': 659896}
{'id': 702292}
{'id': 692639}
{'id': 688544}
{'id': 680936}
{'id': 664296}
{'id': 701207}
{'id': 701

{'id': 645261}
{'id': 586351}
{'id': 698436}
{'id': 686442}
{'id': 684398}
{'id': 695803}
{'id': 673794}
{'id': 673223}
{'id': 686983}
{'id': 683312}
{'id': 679963}
{'id': 679860}
{'id': 660916}
{'id': 704260}
{'id': 701091}
{'id': 698432}
{'id': 698429}
{'id': 698428}
{'id': 697863}
{'id': 696627}
{'id': 695297}
{'id': 695174}
{'id': 693927}
{'id': 693711}
{'id': 693710}
{'id': 693705}
{'id': 693692}
{'id': 693688}
{'id': 693213}
{'id': 692781}
{'id': 691832}
{'id': 691327}
{'id': 673799}
{'id': 673801}
{'id': 673791}
{'id': 672147}
{'id': 669179}
{'id': 686130}
{'id': 681685}
{'id': 649034}
{'id': 698184}
{'id': 687862}
{'id': 686993}
{'id': 686990}
{'id': 686987}
{'id': 686984}
{'id': 686979}
{'id': 686977}
{'id': 686976}
{'id': 686971}
{'id': 686970}
{'id': 686969}
{'id': 686968}
{'id': 686931}
{'id': 686002}
{'id': 685997}
{'id': 684915}
{'id': 684355}
{'id': 683355}
{'id': 673787}
{'id': 643367}
{'id': 705711}
{'id': 697317}
{'id': 691119}
{'id': 692552}
{'id': 684208}
{'id': 681

{'id': 688691}
{'id': 688681}
{'id': 688678}
{'id': 688673}
{'id': 688657}
{'id': 688651}
{'id': 688613}
{'id': 688600}
{'id': 688593}
{'id': 688591}
{'id': 688584}
{'id': 688578}
{'id': 688551}
{'id': 688498}
{'id': 688493}
{'id': 688485}
{'id': 688422}
{'id': 688416}
{'id': 688406}
{'id': 688397}
{'id': 688396}
{'id': 688393}
{'id': 688392}
{'id': 688388}
{'id': 688354}
{'id': 688348}
{'id': 688325}
{'id': 688323}
{'id': 688252}
{'id': 688242}
{'id': 688233}
{'id': 688232}
{'id': 688231}
{'id': 688229}
{'id': 688228}
{'id': 688227}
{'id': 688226}
{'id': 688225}
{'id': 688224}
{'id': 688222}
{'id': 688217}
{'id': 688198}
{'id': 688173}
{'id': 688146}
{'id': 688136}
{'id': 688103}
{'id': 688083}
{'id': 688047}
{'id': 688029}
{'id': 688027}
{'id': 687998}
{'id': 687960}
{'id': 687941}
{'id': 687827}
{'id': 687765}
{'id': 687759}
{'id': 687742}
{'id': 687735}
{'id': 687646}
{'id': 687643}
{'id': 687614}
{'id': 687613}
{'id': 687602}
{'id': 687577}
{'id': 687574}
{'id': 687570}
{'id': 687

{'id': 676459}
{'id': 676434}
{'id': 676428}
{'id': 676419}
{'id': 676388}
{'id': 676347}
{'id': 676276}
{'id': 676274}
{'id': 676270}
{'id': 676220}
{'id': 676178}
{'id': 676144}
{'id': 675895}
{'id': 675887}
{'id': 675860}
{'id': 675859}
{'id': 675839}
{'id': 675829}
{'id': 675828}
{'id': 675827}
{'id': 675754}
{'id': 675537}
{'id': 675528}
{'id': 675506}
{'id': 675502}
{'id': 675477}
{'id': 675468}
{'id': 675453}
{'id': 675441}
{'id': 675380}
{'id': 675378}
{'id': 675359}
{'id': 675356}
{'id': 675333}
{'id': 675331}
{'id': 675328}
{'id': 675313}
{'id': 675282}
{'id': 675280}
{'id': 675270}
{'id': 675242}
{'id': 675239}
{'id': 675152}
{'id': 675150}
{'id': 675118}
{'id': 675113}
{'id': 675051}
{'id': 675038}
{'id': 675031}
{'id': 674965}
{'id': 674964}
{'id': 674947}
{'id': 674930}
{'id': 674918}
{'id': 674899}
{'id': 674889}
{'id': 674883}
{'id': 674869}
{'id': 674858}
{'id': 674857}
{'id': 674856}
{'id': 674827}
{'id': 674821}
{'id': 674819}
{'id': 674725}
{'id': 674723}
{'id': 674

In [215]:
similar_movie_id_df = pd.DataFrame(similar_movie_id_dict_list)

In [216]:
similar_movie_id_df

id                                   similar_movie_id
0     385103  [11459, 18885, 61979, 50544, 449176, 177572, 1...
1     338762  [246655, 68721, 9738, 299537, 1726, 10138, 383...
2     582596  [8914, 1907, 578, 480105, 345940, 492336, 1769...
3     454626  [207703, 634649, 49530, 550988, 399566, 338970...
4     545609  [505642, 447365, 634649, 383498, 566525, 58048...
...      ...                                                ...
5627  671901                                                 []
5628  671897  [150540, 10555, 62177, 109445, 812, 326359, 21...
5629  671895  [150540, 62177, 10555, 109445, 812, 326359, 21...
5630  671893                                                 []
5631  671891                                                 []

[5632 rows x 2 columns]

In [218]:
movie_info_with_similar_df = pd.merge(s_movie_info_df, similar_movie_id_df, how='inner', on='id', right_index=False, sort=True)

In [219]:
movie_info_with_similar_df.to_csv('data/movie_with_similar_010120_050120.csv', index=False)

In [207]:
for i in range(len(movie_id_list)):
    if movie_id_list[i]['id'] == 663064:
        print(i)

1005


In [220]:
s_movie_id_add_list = []
for n in similar_movie_id_dict_list:
    s_movie_id_add_list = s_movie_id_add_list + n['similar_movie_id']

In [222]:
s_movie_id_add_set = set(s_movie_id_add_list)

In [223]:
s_movie_id_add_set

{2,
 131074,
 5,
 6,
 9,
 12,
 13,
 14,
 262156,
 16,
 15,
 18,
 19,
 20,
 21,
 22,
 24,
 26,
 27,
 28,
 30,
 32,
 33,
 655394,
 35,
 38,
 55,
 58,
 59,
 62,
 63,
 64,
 65,
 66,
 67,
 68,
 69,
 70,
 71,
 73,
 74,
 75,
 262220,
 77,
 78,
 79,
 80,
 81,
 82,
 83,
 524370,
 85,
 86,
 87,
 88,
 89,
 90,
 393306,
 91,
 93,
 262234,
 95,
 96,
 97,
 98,
 99,
 524381,
 101,
 102,
 103,
 104,
 105,
 106,
 107,
 131177,
 108,
 110,
 111,
 113,
 114,
 115,
 116,
 117,
 118,
 131185,
 120,
 121,
 122,
 131193,
 393340,
 125,
 127,
 128,
 129,
 393345,
 132,
 133,
 134,
 135,
 136,
 137,
 138,
 139,
 140,
 141,
 142,
 143,
 144,
 145,
 524434,
 147,
 146,
 149,
 148,
 655508,
 152,
 153,
 393368,
 155,
 156,
 158,
 262303,
 160,
 161,
 162,
 163,
 164,
 165,
 393380,
 167,
 168,
 169,
 170,
 171,
 166,
 173,
 524461,
 175,
 176,
 177,
 178,
 179,
 180,
 174,
 182,
 183,
 184,
 185,
 186,
 187,
 189,
 192,
 655552,
 194,
 195,
 196,
 197,
 198,
 199,
 200,
 201,
 204,
 205,
 207,
 211,
 212,
 213,
 

In [225]:
print(len(s_movie_id_add_list))
print(len(s_movie_id_add_set))

124869
25100


In [253]:
import json
def save_json(data):
    #jsonData = json.dumps(data)
    with open('data/similar_movie_info.json') as json_file: 
        load_data = json.load(json_file) 
        temp = load_data['similar_movie_info'] 

        # appending data to emp_details  
        temp.append(data) 

    with open('data/similar_movie_info.json', 'w') as outfile:
        json.dump({'similar_movie_info':temp}, outfile) 

In [254]:
%%time
s_movie_info_list = []
for n in s_movie_id_add_set:
    s_movie_req = requests.get("https://api.themoviedb.org/3/movie/"+str(n)+"?api_key="+my_api_key)
    s_movie_req_j = s_movie_req.json()
    if s_movie_req_j != {'status_code': 34, 'status_message': 'The resource you requested could not be found.'}:
        data = {'id': s_movie_req_j['id'], 
                "vote_average": s_movie_req_j["vote_average"], 
                'vote_count': s_movie_req_j['vote_count'],
                "title": s_movie_req_j["title"], 
                "genre_id": [g['id'] for g in s_movie_req_j["genres"]], 
                "overview": s_movie_req_j["overview"], 
                'popularity': s_movie_req_j['popularity'], 
                'original_language': s_movie_req_j['original_language'], 
                'release_date': s_movie_req_j['release_date'], 
                "production_companies_id": [p['id'] for p in s_movie_req_j["production_companies"]], 
                "homepage": s_movie_req_j["homepage"], 
                "imdb_id": s_movie_req_j["imdb_id"], 
                "revenue": s_movie_req_j["revenue"], 
                "tagline": s_movie_req_j["tagline"]}
        save_json(data)
#         s_movie_info_list.append({'id': s_movie_req_j['id'], 
#                            "vote_average": s_movie_req_j["vote_average"], 
#                            'vote_count': s_movie_req_j['vote_count'],
#                            "title": s_movie_req_j["title"], 
#                            "genre_id": [g['id'] for g in s_movie_req_j["genres"]], 
#                            "overview": s_movie_req_j["overview"], 
#                            'popularity': s_movie_req_j['popularity'], 
#                            'original_language': s_movie_req_j['original_language'], 
#                            'release_date': s_movie_req_j['release_date'], 
#                            "production_companies_id": [p['id'] for p in s_movie_req_j["production_companies"]], 
#                            "homepage": s_movie_req_j["homepage"], 
#                            "imdb_id": s_movie_req_j["imdb_id"], 
#                            "revenue": s_movie_req_j["revenue"], 
#                            "tagline": s_movie_req_j["tagline"]})


ConnectionError: ('Connection aborted.', OSError("(54, 'ECONNRESET')"))

In [267]:
s_m_l

TypeError: 'set' object is not subscriptable

In [284]:
s_m_l = []

with open('data/similar_movie_info.json') as json_file:
    data = json.load(json_file)
    for p in data['similar_movie_info']:
        s_m_l.append(p)

In [285]:
len(s_m_l)

25087

In [259]:
len(s_movie_id_add_set)

25100

In [286]:
sml_df = pd.DataFrame(s_m_l)

In [269]:
current_sm_id_list = sml_df['id'].tolist()

In [273]:
rest_sm_id_set = s_movie_id_add_set - set(current_sm_id_list)

In [281]:
rest_sm_id_set = rest_sm_id_set - {360542}

In [282]:
len(rest_sm_id_set)

8665

In [287]:
sml_df.to_csv('data/similar_m_info.csv', index=False)

In [283]:
for n in rest_sm_id_set:
    print(n)
    s_movie_req = requests.get("https://api.themoviedb.org/3/movie/"+str(n)+"?api_key="+my_api_key)
    s_movie_req_j = s_movie_req.json()
    if s_movie_req_j != {'status_code': 34, 'status_message': 'The resource you requested could not be found.'}:
        data = {'id': s_movie_req_j['id'], 
                "vote_average": s_movie_req_j["vote_average"], 
                'vote_count': s_movie_req_j['vote_count'],
                "title": s_movie_req_j["title"], 
                "genre_id": [g['id'] for g in s_movie_req_j["genres"]], 
                "overview": s_movie_req_j["overview"], 
                'popularity': s_movie_req_j['popularity'], 
                'original_language': s_movie_req_j['original_language'], 
                'release_date': s_movie_req_j['release_date'], 
                "production_companies_id": [p['id'] for p in s_movie_req_j["production_companies"]], 
                "homepage": s_movie_req_j["homepage"], 
                "imdb_id": s_movie_req_j["imdb_id"], 
                "revenue": s_movie_req_j["revenue"], 
                "tagline": s_movie_req_j["tagline"]}
        save_json(data)

360551
491625
98416
491633
65653
491657
491664
458897
589970
229531
360604
65707
458927
590006
360631
360633
360637
360639
360640
327876
360648
98514
360659
360663
458969
65754
65759
458991
491760
491761
590065
360689
196852
491766
98551
327928
327930
590079
459008
196867
98566
327944
98568
622868
590102
327958
459039
65828
65829
196906
196907
590129
360760
98616
229693
98631
98632
590153
328012
590157
196942
328014
98639
360784
590162
590164
590167
65881
590172
360799
65889
328037
459109
360811
360814
491887
65904
229746
229749
459137
622977
65931
590219
459151
328079
360847
491930
623002
65951
65953
590242
623013
197033
459181
328111
197044
459189
491959
229821
229823
65994
459214
623057
459224
360920
197082
360927
590306
492005
492008
66027
492015
590320
328179
197112
459258
623104
328193
623106
459278
459279
328216
623131
459295
459297
623138
623141
360997
98864
66100
66101
66105
328252
492096
66121
229962
66125
66127
623183
66129
66131
197206
459350
492118
459362
361060
361069
459

495983
364915
463220
201085
201088
70018
332162
332163
332168
627081
70027
627093
233879
463256
463257
594342
463272
70067
70074
496059
70076
627133
463299
70089
463315
102867
70104
365018
463325
627168
365024
70114
70115
463337
102890
332270
102899
365045
70135
365048
463353
332283
70160
332308
234004
332311
332340
70196
70198
496189
332356
70214
496212
70233
332384
594530
463468
496243
332409
234105
332411
365179
234112
103046
463500
201363
496285
103071
365222
70322
234165
496310
70327
103093
627381
332479
70342
103117
365265
103122
70358
332502
234200
201434
201439
234207
70372
234212
594663
103156
463607
496375
594685
103166
594687
627456
594689
365315
627465
627468
103181
332562
627475
627477
332567
627482
103195
627485
627487
627489
365350
365351
365355
365356
103213
365358
365367
463684
594759
70489
627553
594791
594799
594809
201593
103298
365448
103314
365458
332703
627616
332706
332712
70578
70580
627654
201676
463821
332749
201684
201686
627671
463833
463843
201703
70635
36

468033
369733
369735
238664
336972
599139
468071
369769
369770
74860
468080
500848
500852
500853
238713
74879
533637
238726
337039
74899
337048
369821
238751
500899
599204
500904
631982
500919
74945
369858
74948
599241
599242
599244
74958
599247
337104
599249
599251
599252
369876
599254
599257
238810
369883
599260
369885
599262
599264
599265
599266
599267
107751
599273
599274
468201
500970
599277
599278
468207
468210
599284
74997
599290
369914
75004
107775
468224
337154
337155
238850
369927
599309
238861
337167
337170
337186
107811
238896
337204
369972
501050
107837
632133
107846
369992
238921
238923
369997
206159
599379
206167
337254
632171
468332
238958
370031
206192
238959
468339
468361
468362
337299
337300
75159
206237
501150
337313
75174
501158
239023
107952
239025
501170
75190
206262
337339
370112
599499
206284
206289
107985
107987
239059
468446
599521
599528
370158
468464
206324
337401
75258
337404
337405
599550
370172
239103
501251
206349
75282
108055
75300
75301
468522
468531


79179
79181
243022
505177
472414
374111
111969
79203
243046
472424
505192
341366
79224
603519
374144
472451
472454
374150
374151
505225
79242
341390
243086
79252
636311
603551
505247
603561
505262
374191
472502
636344
374205
374206
210384
79316
79319
603608
374232
79326
472553
374251
374252
472573
112131
79364
79365
79378
79382
505366
472608
112160
112162
341540
472612
243238
505386
603692
210479
341553
341558
636474
472640
636481
341571
112200
210506
112202
112205
112211
79458
472674
636517
669287
636522
79470
603761
505458
505464
79495
374408
472714
472715
210577
505500
472734
79519
374440
210605
341687
79544
341689
472761
374455
79548
374461
374464
79553
505537
374470
505543
374475
702158
112336
636632
472796
374493
505568
112355
374499
472817
505600
374533
210695
636679
603916
374543
79634
374547
79640
210719
79649
505642
210733
210737
636727
112454
243526
79694
374607
374609
603991
505687
112473
374617
79707
374630
79721
505706
341870
243568
79735
341881
472954
636793
79749
112529

345888
116515
116517
476968
345897
83756
378672
83761
116529
378674
378676
345911
83770
345914
345916
345920
608065
345922
83781
378695
608079
345937
345938
345940
83797
83805
116577
477033
83817
83827
116599
116603
116614
608136
83857
83860
83868
509853
116641
83875
83880
477098
509874
346036
214967
83896
477114
83899
346045
509910
116695
116698
608221
346079
215012
116711
116712
116719
247794
346102
608249
247802
83965
83973
116745
378891
83989
346134
83995
346146
84005
378925
84014
116800
215105
477251
116808
641097
378954
378952
378957
510034
378962
346202
84060
346204
84062
346205
346206
346207
84071
378984
116842
247914
378991
84081
84087
510073
84093
84097
477313
84100
116868
84105
477331
379029
641177
510111
379040
215211
84140
510139
608444
641213
84165
84168
84169
84174
84175
379088
84178
84179
84184
84185
477403
84188
84190
84199
84200
248042
477425
116979
641270
116982
510200
116986
346364
608512
84226
215299
346372
215303
477447
379149
215313
510228
215318
84246
215322
842

88534
383458
121342
612863
612866
88580
383498
350741
121369
88602
481820
350754
383526
121390
383538
481848
88633
514619
88651
383566
219731
481877
252501
88665
252512
383585
252522
481918
481937
121491
514710
645786
645789
481952
252579
350893
88765
350910
514752
514754
514755
350916
252611
383682
481999
613073
482004
88794
482017
219874
514787
514793
613099
219889
514813
613119
482048
121606
645894
252680
88842
121613
252693
514847
88865
482082
252708
121636
88870
482091
383788
219951
482099
351037
88893
252735
351044
482121
514889
383821
121677
383829
219990
88920
351065
613210
351067
351064
121695
383841
482150
121702
514921
613235
613248
121734
482192
482193
514960
252822
514968
252838
89008
252853
514999
515001
121789
220094
252865
121803
613324
351187
482262
252889
89057
515042
121826
613348
646117
351211
121835
252914
646132
121845
121848
220153
121850
252924
121856
384002
89091
482308
252932
351242
646155
351245
121869
220176
121872
252945
121873
121875
384018
89116
121890
25

486659
224517
126219
257291
93456
93457
617749
388374
126230
93465
486684
617759
617760
355621
355623
617768
617770
126250
388399
617782
617784
617786
257344
257345
93507
126277
126278
355655
126286
93521
355672
93529
126315
126319
388473
126331
617859
126363
257444
257445
257447
126376
355758
93629
257475
617924
126411
486861
650706
486869
617945
355805
486879
126432
486882
617956
93672
388591
126451
224763
650747
486912
650755
519689
126487
257566
618019
486949
519729
355890
126526
93768
519759
355921
618110
93828
93837
257678
388757
388764
356000
93856
487083
356021
356022
224950
224972
257747
388819
519894
126683
257769
519918
388850
618228
388854
487161
257785
93950
388862
225044
388885
225052
126749
126757
388908
94005
356156
126781
487242
356175
520016
388963
356199
618344
356200
618352
126839
487301
257932
651151
126864
618389
389015
94104
389030
126889
356274
520134
487369
126923
356301
126926
356305
225235
651220
126938
487387
356326
94183
356330
126955
356332
520172
356335
2

458156
64942
327087
490927
622001
458166
196024
589240
359871
523711
327107
97731
97734
130507
196044
228813
261593
228831
589291
261618
65013
65017
359934
523777
97795
359940
228869
491014
327175
261641
65034
458253
261647
523792
65041
523798
622109
65055
359968
196127
65057
65058
327210
523818
491052
491060
589366
589367
359990
327225
654902
65083
458300
359997
65086
523832
196160
458305
228931
392772
228933
458310
622151
622152
130629
523845
523849
97870
327249
622161
622165
392789
622167
65114
97883
360029
196193
97889
458339
458343
458344
622185
228970
228967
392807
228973
654954
65137
458356
97910
65146
622203
491132
654974
228991
458371
261768
97933
261776
523931
65186
65192
491178
196269
458414
130737
65203
360115
97972
130739
458423
65207
97975
261814
261818
65214
491199
130750
261823
327362
65218
261825
97989
130754
392900
261832
392906
589515
65228
65229
229069
655054
65233
392918
261848
327392
261856
261860
65255
589545
98025
98028
458481
392955
360188
458506
65291
491277
9

In [280]:
s_movie_req = requests.get("https://api.themoviedb.org/3/movie/360542?api_key="+my_api_key)
#s_movie_req_j = s_movie_req.json()
s_movie_req

<Response [504]>

In [229]:
s_movie_req_j

{'adult': False,
 'backdrop_path': '/kpuTCMw3v2AuKjqGS7383uWbc8V.jpg',
 'belongs_to_collection': None,
 'budget': 0,
 'genres': [{'id': 18, 'name': 'Drama'},
  {'id': 80, 'name': 'Crime'},
  {'id': 35, 'name': 'Comedy'}],
 'homepage': '',
 'id': 2,
 'imdb_id': 'tt0094675',
 'original_language': 'fi',
 'original_title': 'Ariel',
 'overview': "Taisto Kasurinen is a Finnish coal miner whose father has just committed suicide and who is framed for a crime he did not commit. In jail, he starts to dream about leaving the country and starting a new life. He escapes from prison but things don't go as planned...",
 'popularity': 8.866,
 'poster_path': '/ojDg0PGvs6R9xYFodRct2kdI6wC.jpg',
 'production_companies': [{'id': 2303,
   'logo_path': None,
   'name': 'Villealfa Filmproductions',
   'origin_country': 'FI'}],
 'production_countries': [{'iso_3166_1': 'FI', 'name': 'Finland'}],
 'release_date': '1988-10-21',
 'revenue': 0,
 'runtime': 73,
 'spoken_languages': [{'iso_639_1': 'de', 'name': 'Deu

In [208]:
movie_id_list[1006]

{'id': 701515}

In [ ]:
similar_page_number = movie_2['total_pages']
similar_movie_number = movie_2['total_results']
similar_movie_id_list = []